# Caminantes Blancos

In [33]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML
from scipy.integrate import solve_ivp

In [ ]:
N = 2000000        # Población total
tr = 100         #Transmisibilidad
k = 2           #Contactos de individuo infectado
dias_de_incubacion = 0.1
o = 1/dias_de_incubacion        #Tasa de progresion a infeccioso
b = k*tr       
beta = b/N     # Tasa de transmisión
gamma = 0.05     # Tasa de recuperación
D = 1/gamma     # Duración promedio de la infección

muro = True
WinterIsComming = 140
Invierno = False



In [42]:
I0 = 100000                # Infectados iniciales
E0 = 0                # Expuestos iniciales
R0 = 0                # Recuperados iniciales
S0 = N - I0 - R0 - E0 # Susceptibles iniciales

In [43]:
t_max = 250
dt = 0.5   # Paso más grande para que la animación sea más rápida
t = np.linspace(0, t_max, int(t_max/dt))
step = 5

In [44]:
def deriv(y, t, N, beta, gamma,o):
    S, E, I, R = y
    dSdt = -beta * S * I /N
    dEdt = beta * S * I/N - (o * E)
    dIdt = (o * E) - gamma * I
    dRdt = gamma * I
    return dSdt, dEdt, dIdt, dRdt

In [45]:
# SciPy solve_ivp 
def rk45(N, beta, gamma,o, S0, E0, I0, R0, t):
    def seir(t, y): return deriv(y, t, N, beta, gamma,o)
    sol = solve_ivp(seir, (t[0], t[-1]), [S0, E0, I0, R0], t_eval=t, method='RK45')
    return sol.y[0], sol.y[1], sol.y[2], sol.y[3]


In [46]:
S,E,I,R = rk45(N,beta,gamma,o,S0,E0,I0,R0,t)

In [48]:
fig, ax = plt.subplots(figsize=(8,5))
ax.set_xlim(0, t_max)
ax.set_ylim(0, N)
ax.set_xlabel("Tiempo (días)")
ax.set_ylabel("Número de individuos")
ax.set_title("Modelo SEIR")

lineS, = ax.plot([], [], 'b-', lw=2, label="Susceptibles")
lineE, = ax.plot([], [], 'orange', lw=2, label="Expuestos") 
lineI, = ax.plot([], [], 'r-', lw=2, label="Infectados")
lineR, = ax.plot([], [], 'g-', lw=2, label="Recuperados")
ax.legend()

# Puntos en la punta de cada curva
pointS, = ax.plot([], [], 'bo')
pointE, =  ax.plot([], [], 'o', color='orange', markersize=6)
pointI, = ax.plot([], [], 'ro')
pointR, = ax.plot([], [], 'go')

# Textos dinámicos con estilo (más grandes y con círculo)
textS = ax.text(0,0,'',color='blue', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='blue', boxstyle='circle,pad=0.4'))
textE = ax.text(0,0,'',color='yellow', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='yellow', boxstyle='circle,pad=0.4'))
textI = ax.text(0,0,'',color='red', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='red', boxstyle='circle,pad=0.4'))
textR = ax.text(0,0,'',color='green', fontsize=12,
                bbox=dict(facecolor='white', edgecolor='green', boxstyle='circle,pad=0.4'))

def init():
    lineS.set_data([], [])
    lineE.set_data([], [])
    lineI.set_data([], [])
    lineR.set_data([], [])
    pointS.set_data([], [])
    pointE.set_data([], [])
    pointI.set_data([], [])
    pointR.set_data([], [])
    textS.set_text('')
    textE.set_text('')
    textI.set_text('')
    textR.set_text('')
    return lineS, lineE, lineI, lineR, pointS, pointE, pointI, pointR, textS, textE, textI, textR

def update(frame):

    idx = frame * step
    if idx >= len(t):
        idx = len(t)-1
    
    # Actualizar curvas
    lineS.set_data(t[:idx], S[:idx])
    lineE.set_data(t[:idx], E[:idx])
    lineI.set_data(t[:idx], I[:idx])
    lineR.set_data(t[:idx], R[:idx])
    
    # Actualizar puntos
    pointS.set_data([t[idx]], [S[idx]])
    pointE.set_data([t[idx]], [E[idx]])
    pointI.set_data([t[idx]], [I[idx]])
    pointR.set_data([t[idx]], [R[idx]])
    
    # Actualizar textos (desplazados a la derecha)
    textS.set_position((t[idx]+2, S[idx]))
    textS.set_text(f"{S[idx]:.0f}")
    textE.set_position((t[idx]+2, E[idx]))
    textE.set_text(f"{E[idx]:.0f}")
    textI.set_position((t[idx]+2, I[idx]))
    textI.set_text(f"{I[idx]:.0f}")
    textR.set_position((t[idx]+2, R[idx]))
    textR.set_text(f"{R[idx]:.0f}")
    
    return lineS,lineE, lineI, lineR, pointS, pointE, pointI, pointR, textS, textE, textI, textR

ani = FuncAnimation(fig, update, frames=len(t)//step, init_func=init,
                    blit=True, interval=100, repeat=False)
plt.close()
HTML(ani.to_jshtml())
